# **RYP COMING PAYMENT**

**Load Spreadsheet RYP**

In [ ]:
import gspread
from oauth2client.service_account import ServiceAccountCredentials
import pandas as pd

# 1. Tentukan scope untuk akses ke Google Sheets dan Drive
scope = [
    "https://spreadsheets.google.com/feeds",
    "https://www.googleapis.com/auth/drive"
]

# 2. Load file credentials JSON (ganti namanya kalau beda)
creds = ServiceAccountCredentials.from_json_keyfile_name("/home/houseofom/public_html/offline_sales/API/spreadsheet-439003-68ab13b2ce0d.json", scope)
client = gspread.authorize(creds)

# 3. Buka spreadsheet by URL
spreadsheet = client.open_by_url("https://docs.google.com/spreadsheets/d/1MCSFOD7uKJ-TJ_srMQqrK277QgWYBWKDkk5jk4ofJaM")

# 4. Akses worksheet 'MONTHLY (2025)'
sheet = spreadsheet.worksheet("MONTHLY (2025)")

# 5. Ambil semua data
records = sheet.get_all_records()

# 6. Ubah ke DataFrame
df_ryp = pd.DataFrame(records)

# 7. Tampilkan 5 baris awal
print(df_ryp.head())


  NO PAYMENT GATEWAY                                     TRANSACTION ID  \
0  1          XENDIT  ptaumb-d608690763824b71-8da9b15cc8c5917e-17356...   
1  2          XENDIT                                      INV8825066499   
2  3          XENDIT  ptaumb-74494f2a08cf4716-89ae6a281254575c-17357...   
3  4          XENDIT  ptaumb-b59793e889bc44a3-9dbe892e58f24143-17357...   
4  5          PAYPAL                                  1P957061EJ8591743   

  DATE OF PAYMENT PRODUCT PRICE (USD) AMOUNT PAID (IDR) AMOUNT PAID (USD)  \
0     01-Jan-2025              2100.0          27490700            1700.0   
1     01-Jan-2025              2100.0           6674400             400.0   
2     02-Jan-2025              2100.0          27665800            1700.0   
3     02-Jan-2025              2100.0          14183100             850.0   
4      7-Jan-2025                2100           6375721             382.1   

  AMOUNT PAID (INR)             NAME                    EMAIL COURSE SCHEDULE  \
0    

**Cleansing Data**

In [3]:
# 1. Konversi kolom DATE OF PAYMENT ke datetime (aman jika format beragam)
df_ryp['DATE OF PAYMENT'] = pd.to_datetime(df_ryp['DATE OF PAYMENT'], errors='coerce')

# 2. Hapus kolom 'NO' dan kolom tanpa nama / kosong
df_ryp.drop(columns=['NO'], inplace=True, errors='ignore')
df_ryp = df_ryp.loc[:, ~df_ryp.columns.str.contains('^Unnamed|^\\s*$')]

# 3. Tambahkan kolom YEAR dari DATE OF PAYMENT, pastikan integer (Int64 untuk dukung NaN)
df_ryp.insert(0, 'YEAR', df_ryp['DATE OF PAYMENT'].dt.year.astype('Int64'))
df_ryp.insert(1, 'MONTH', df_ryp['DATE OF PAYMENT'].dt.month.astype('Int64'))

In [4]:
df_ryp.dropna(subset=['YEAR', 'MONTH', 'DATE OF PAYMENT'], inplace=True)

In [5]:
# Simpan nilai asli sebagai backup (jika perlu audit)
df_ryp['COURSE_SCHEDULE_RAW'] = df_ryp['COURSE SCHEDULE'].astype(str)

# Coba konversi awal ke datetime (untuk melihat anomali nantinya)
df_ryp['COURSE_SCHEDULE_PARSED'] = pd.to_datetime(
    df_ryp['COURSE_SCHEDULE_RAW'],
    errors='coerce',
    dayfirst=True
)

In [6]:
# Flag data yang tidak valid / tidak masuk akal (misal: tahun sebelum 2020)
anomaly_mask = (
    df_ryp['COURSE_SCHEDULE_PARSED'].isna() |
    (df_ryp['COURSE_SCHEDULE_PARSED'].dt.year < 2020)
)

# Lihat semua yang aneh
print(">> Data anomali:")
print(df_ryp.loc[anomaly_mask, ['COURSE_SCHEDULE_RAW']])

>> Data anomali:
    COURSE_SCHEDULE_RAW
131            5 Aug 25
199          23-10-2025


In [7]:
import re
from dateutil import parser

# Fungsi perbaikan + parsing aman
def parse_course_schedule(val):
    if not isinstance(val, str):
        return pd.NaT

    # 1. Perbaiki tahun typo: 1015, 1025 → 2025
    fixed = re.sub(r'(\d{1,2}\s*[A-Za-z]{3,9}\s*)1\d{3}', r'\g<1>2025', val)

    # 2. Coba parse dengan dateutil parser (fleksibel, bisa handle semua format)
    try:
        return parser.parse(fixed, dayfirst=True)
    except:
        return pd.NaT

# Terapkan ke kolom
df_ryp['COURSE SCHEDULE'] = df_ryp['COURSE SCHEDULE'].astype(str).apply(parse_course_schedule)

In [8]:
df_ryp.drop(columns=[
    'COURSE_SCHEDULE_RAW',
    'COURSE_SCHEDULE_PARSED',
    'DATE'
], inplace=True)


**OUTPUT**

In [9]:
df_ryp

YEAR  MONTH PAYMENT GATEWAY  \
0    2025      1          XENDIT   
1    2025      1          XENDIT   
2    2025      1          XENDIT   
3    2025      1          XENDIT   
4    2025      1          PAYPAL   
..    ...    ...             ...   
203  2025      6          XENDIT   
204  2025      6          XENDIT   
205  2025      6          XENDIT   
206  2025      6          PAYPAL   
207  2025      6          PAYPAL   

                                        TRANSACTION ID DATE OF PAYMENT  \
0    ptaumb-d608690763824b71-8da9b15cc8c5917e-17356...      2025-01-01   
1                                        INV8825066499      2025-01-01   
2    ptaumb-74494f2a08cf4716-89ae6a281254575c-17357...      2025-01-02   
3    ptaumb-b59793e889bc44a3-9dbe892e58f24143-17357...      2025-01-02   
4                                    1P957061EJ8591743      2025-01-07   
..                                                 ...             ...   
203  CS-ptaumb-d28555736b404961-aac5a45da7096de3-17...      2025-06-07   
204  ptaumb-dafc5e6fc6924f3e-96f90db2b67fce4e-17493...      2025-06-08   
205  CS-ptaumb-14d6587e52834969-afb9b6c59e429dcf-17...      2025-06-11   
206                                  0AH5026355419103V      2025-06-11   
207                                  7JD468093T809652F      2025-06-11   

    PRODUCT PRICE (USD) AMOUNT PAID (IDR) AMOUNT PAID (USD) AMOUNT PAID (INR)  \
0                2100.0          27490700            1700.0                     
1                2100.0           6674400             400.0                     
2                2100.0          27665800            1700.0                     
3                2100.0          14183100             850.0                     
4                  2100           6375721             382.1                     
..                  ...               ...               ...               ...   
203                2500         9032070.0             555.0                     
204                2500        32854940.0            1945.0                     
205                2500        32854940.0            1945.0                     
206              2100.0                             1859.12                     
207              2100.0                               83.83                     

                             NAME                    EMAIL COURSE SCHEDULE  \
0                    Twinsa Patel    twinsapatel@yahoo.com      2025-01-26   
1                 Isabella Reimer   ireimer12076@gmail.com      2025-07-07   
2                  Felicia Jitaru  feliciajitaru@yahoo.com      2025-01-26   
3                      Pippa Ryan    pipparyan98@gmail.com      2025-01-26   
4                    Leah Bromley     Leahbrom91@gmail.com      2025-03-21   
..                            ...                      ...             ...   
203                Felicia Cheong   felcolette@hotmail.com      2025-07-29   
204                Felicia Cheong   felcolette@hotmail.com      2025-07-29   
205  Maria Elisa Arroyo Hernandez  elisaarroyo92@gmail.com      2025-07-29   
206                    ANNA ASKEW     ANNAKASKEW@GMAIL.COM      2025-09-21   
207                    Anna Askew     annakaskew@gmail.com      2025-09-21   

    PRODUCT TYPE            PAYMENT NOTES PROMO NOTES               SITES  \
0     200HR-TWIN        Remaining Payment              Rishikesh Yogpeeth   
1     200HR-TWIN                  Deposit              Rishikesh Yogpeeth   
2     200HR-TWIN        Remaining Payment              Rishikesh Yogpeeth   
3     200HR-TWIN  Split Remaining Payment              Rishikesh Yogpeeth   
4     200HR-TWIN                  Deposit              Rishikesh Yogpeeth   
..           ...                      ...   ...   ...                 ...   
203   300HR-TWIN                  Deposit              Rishikesh Yogpeeth   
204   300HR-TWIN        Remaining Payment              Rishikesh Yogpeeth   
205   300HR-TWIN        Remaining Payment              Rishikesh Yogpeeth   
206

# **HOM COMING PAYMENT**

**Load Spreadsheet HOM**

In [10]:
import pandas as pd
import requests
from io import BytesIO

# File ID dari spreadsheet Excel yang di-upload
file_id = "1TjAk0eGWv7AhsoTqWsL6Wn7UR5p3mvGa"
download_url = f"https://drive.google.com/uc?export=download&id={file_id}"

# Request file dari Google Drive
response = requests.get(download_url)

# Baca sebagai Excel dari memori (tanpa simpan ke file)
df_hom = pd.read_excel(BytesIO(response.content), sheet_name="MONTHLY (2025)")

# Tampilkan hasil
print(df_hom.head())


        NO PAYMENT GATEWAY                              TRANSACTION ID  \
0  JANUARY             NaN                                         NaN   
1        1          XENDIT  CS-Celestial-Renewal-Deposit-1735663477779   
2        2          XENDIT                               INV6498867006   
3        3          XENDIT                               INV7204857432   
4        4          XENDIT                               INV5648269840   

  DATE OF PAYMENT  PRODUCT PRICE (USD) AMOUNT PAID (IDR) AMOUNT PAID (USD)  \
0             NaT                  NaN               NaN               NaN   
1      2025-01-01               2470.0           6674400               400   
2      2025-01-01               2135.0           6674400               400   
3      2025-01-01               1590.0          26530740              1590   
4      2025-01-01               1855.0           6674400               400   

   AMOUNT PAID (EUR)          NAME                      EMAIL  \
0                NaN 

**Cleansing Data**

In [11]:
# 1. Konversi 'DATE OF PAYMENT' ke datetime (kalau belum)
df_hom['DATE OF PAYMENT'] = pd.to_datetime(df_hom['DATE OF PAYMENT'], errors='coerce')

# 2. Hapus kolom 'NO' dan kolom kosong tanpa nama (jika ada)
df_hom.drop(columns=['NO'], inplace=True, errors='ignore')
df_hom = df_hom.loc[:, ~df_hom.columns.str.contains('^Unnamed|^\\s*$', regex=True)]

# 3. Tambahkan kolom YEAR dari 'DATE OF PAYMENT' (bertipe Int64)
df_hom.insert(0, 'YEAR', df_hom['DATE OF PAYMENT'].dt.year.astype('Int64'))
df_hom.insert(1, 'MONTH', df_hom['DATE OF PAYMENT'].dt.month.astype('Int64'))

# Hapus baris yang missing di YEAR, MONTH, atau DATE OF PAYMENT
df_hom.dropna(subset=['YEAR', 'MONTH', 'DATE OF PAYMENT'], inplace=True)

In [12]:
import re
from dateutil import parser

# Fungsi perbaikan + parsing aman untuk COURSE SCHEDULE
def parse_course_schedule(val):
    if not isinstance(val, str):
        return pd.NaT

    # Perbaiki tahun salah ketik: 1015, 1025 → 2025
    fixed = re.sub(r'(\d{1,2}\s*[A-Za-z]{3,9}\s*)1\d{3}', r'\g<1>2025', val)

    try:
        return parser.parse(fixed, dayfirst=True)
    except:
        return pd.NaT

# Terapkan ke kolom COURSE SCHEDULE
df_hom['COURSE SCHEDULE'] = df_hom['COURSE SCHEDULE'].astype(str).apply(parse_course_schedule)

# Hapus baris yang COURSE SCHEDULE-nya tidak valid
df_hom = df_hom[df_hom['COURSE SCHEDULE'].notna()]


In [13]:
df_hom

YEAR  MONTH   PAYMENT GATEWAY  \
1     2025      1            XENDIT   
2     2025      1            XENDIT   
3     2025      1            XENDIT   
4     2025      1            XENDIT   
5     2025      1            XENDIT   
...    ...    ...               ...   
3546  2025      6            XENDIT   
3547  2025      6            XENDIT   
3548  2025      6  BANK_BNI USD 139   
3549  2025      6       EDC_BRI PLG   
3550  2025      6        EDC_BNI TM   

                                         TRANSACTION ID DATE OF PAYMENT  \
1            CS-Celestial-Renewal-Deposit-1735663477779      2025-01-01   
2                                         INV6498867006      2025-01-01   
3                                         INV7204857432      2025-01-01   
4                                         INV5648269840      2025-01-01   
5                                         INV2078740359      2025-01-01   
...                                                 ...             ...   
3546  CS-ptaumb-096804e8fba04dbe-81fcb971da2f6827-17...      2025-06-12   
3547  CS-ptaumb-ef5641ad76064877-aa021a6f188411a7-17...      2025-06-12   
3548                                                NaN      2025-06-09   
3549                                   APPR CODE:D00245      2025-06-12   
3550                                  APPR CODE: PWAR08      2025-06-11   

      PRODUCT PRICE (USD) AMOUNT PAID (IDR) AMOUNT PAID (USD)  \
1                  2470.0           6674400               400   
2                  2135.0           6674400               400   
3                  1590.0          26530740              1590   
4                  1855.0           6674400               400   
5                  3385.0          56440395              3385   
...                   ...               ...               ...   
3546               2295.0           6756800               400   
3547               3020.0          44257040              2620   
3548               3485.0               NaN           3068.02   
3549                  NaN            405000               NaN   
3550                  NaN          12463389               NaN   

      AMOUNT PAID (EUR)                      NAME  \
1                   NaN              KACEY MILLER   
2                   NaN              ALMASS BADAT   
3                   NaN              TSZ WAI PONG   
4                   NaN               KATIE COHEN   
5                   NaN              LINGHUI ZHAO   
...                 ...                       ...   
3546                NaN              Jara Baumann   
3547                NaN            Sylvia Rockman   
3548                NaN       Mathilde Dos Santos   
3549                NaN            Martyna Kocjan   
3550                NaN  Beatriz Muñoz-Cobo Orosa   

                              EMAIL COURSE SCHEDULE   PRODUCT TYPE  \
1         KACEYMILLER7777@GMAIL.COM      2025-01-13     200HR-TWIN   
2            ALMASS@ALMASSBADAT.COM      2025-07-04     200HR-TWIN   
3              PONGTSZWAI@GMAIL.COM      2025-06-30     200HR-DORM   
4                KATII289@GMAIL.COM      2025-07-04   200HR-TRIPLE   
5           ZZZHAOLINGHUI@GMAIL.COM      2025-05-05    200HR-VILLA   
...                             ...             ...            ...   
3546               jara.baum@gmx.de      2025-06-10   200HR-TRIPLE   
3547      sylviarockman03@gmail.com      2025-07-14     200HR-TWIN   
3548    dossantosmathilde@gmail.com      2025-07-14  200HR-PRIVATE   
3549  martyna.anna.kocjan@gmail.com      2025-09-06  200HR-PRIVATE   
3550              bea2660@gmail.com      2025-02-06  200HR-PRIVATE   

            LOCATION      PAYMENT NOTES  \
1        The Mansion            Deposit   
2             Pelaga            Deposit   
3     Melati Cottage       Full Payment   
4      Yoga Amertham            Deposit   
5             Pelaga       Full Payment   
...              ...                ...   
3546   Yoga Amertham            Deposit   
3547     The Mansion  Remaining P

In [14]:
df_ryp.to_excel("data/df_ryp.xlsx", index=False)
df_hom.to_excel("data/df_hom.xlsx", index=False)


In [15]:
# Buat summary function
def generate_summary(df, group_name):
    df = df.copy()
    df['Date of Payment'] = pd.to_datetime(df['DATE OF PAYMENT'], errors='coerce')
    df['Payment Notes'] = df['PAYMENT NOTES'].fillna('(blank)')
    df['AMOUNT PAID (USD)'] = pd.to_numeric(df['AMOUNT PAID (USD)'], errors='coerce').fillna(0)

    # DAILY
    daily = df.pivot_table(index='Payment Notes',
                           columns=df['Date of Payment'].dt.date,
                           values='AMOUNT PAID (USD)',
                           aggfunc='sum',
                           fill_value=0)

    # MONTHLY
    monthly = df.pivot_table(index='Payment Notes',
                             columns=df['Date of Payment'].dt.to_period('M'),
                             values='AMOUNT PAID (USD)',
                             aggfunc='sum',
                             fill_value=0)

    return daily, monthly

# Generate both
daily_ryp, monthly_ryp = generate_summary(df_ryp, "RYP")
daily_hom, monthly_hom = generate_summary(df_hom, "HOM")

# Export summary
daily_ryp.to_excel("data/summary_daily_ryp.xlsx")
monthly_ryp.to_excel("data/summary_monthly_ryp.xlsx")
daily_hom.to_excel("data/summary_daily_hom.xlsx")
monthly_hom.to_excel("data/summary_monthly_hom.xlsx")